In [21]:
kerr_dir = '/work/yifan.wang/ringdown/t7-3ogc_fixpsd/kerr_220.ini'
set_toffset = True
events_dir = './220/events.ini'

In [22]:
import numpy as np
import h5py
import glob
import os

from pycbc.inference.io import loadfile
from pycbc.workflow import WorkflowConfigParser
from pycbc import coordinates,pnutils,conversions

# Generating events.ini from reading posterior files

In [23]:
def get_gwname():
    file = glob.glob('/work/yifan.wang/ringdown/t7-3ogc_fixpsd/3ogc_github_config/*.ini')
    file.remove('/work/yifan.wang/ringdown/t7-3ogc_fixpsd/3ogc_github_config/inference-gw190521_030229_emconstrained.ini')
    gwname = []
    for f in file:
        fname = os.path.basename(f)
        gwname.append(fname.split('-')[1][:15])
    
    #Remove the two GW190521 events and the two BNS events
    gwname.remove('gw170817_124104')
    gwname.remove('gw190425_081805')
    gwname.sort()
    return gwname

gwname = get_gwname()
np.size(gwname)

55

In [24]:
import lal

def info(gwname):
    '''
    The input is like 190521_030229, i.e., remove the 'GW' prefix
    '''
    print(gwname)
    if gwname == '190521_030229':
        h5file=['/work/yifan.wang/3ogcPE/datarelease/allposterior/gr_gw190521.hdf']
    else:
        h5file = glob.glob('/work/yifan.wang/3ogcPE/datarelease/allposterior/*'+str(gwname)+'*.hdf')
    if np.size(h5file)!=1:
        print('Error!!')
    print(h5file)
    f = h5py.File(h5file[0],'r')
    #print(f['samples'].keys())
    #print(f['samples'].keys())
    # ra, dec, mass, t
    i = np.argmax(f['samples']['loglikelihood'][:])
    ra = f['samples']['ra'][i]
    dec = f['samples']['dec'][i]
    tc = f.attrs['trigger_time'] + f['samples']['delta_tc'][i]
    m1 = f['samples']['srcmass1'][i]
    m2 = f['samples']['srcmass2'][i]

    #Cartesian spin
    spin1_x,spin1_y,spin1_z = coordinates.spherical_to_cartesian(f['samples']['spin1_a'][i], \
                                                              f['samples']['spin1_azimuthal'][i],\
                                                              f['samples']['spin1_polar'][i])
    spin2_x,spin2_y,spin2_z = coordinates.spherical_to_cartesian(f['samples']['spin2_a'][i], \
                                                              f['samples']['spin2_azimuthal'][i],\
                                                              f['samples']['spin2_polar'][i])
    # final mass
    final_mass_src = conversions.final_mass_from_initial(mass1=m1,\
                                                   mass2=m2,\
                                                   spin1x=spin1_x,spin1y=spin1_y,spin1z=spin1_z,\
                                                   spin2x=spin2_x,spin2y=spin2_y,spin2z=spin2_z)
        
    z = f['samples']['redshift'][i]
    final_freq = pnutils.get_final_freq('SEOBNRv4',m1*(1+z),m2*(1+z),spin1_z,spin2_z)
    final_mass = final_mass_src*(1+z)
    toffset = 10* final_mass * lal.MTSUN_SI
    f.close()
    return ra,dec,final_mass,final_freq,tc,toffset

In [25]:
try:
    os.remove(events_dir)
except FileNotFoundError:
    pass
with open(events_dir, 'w') as t:
    for n in gwname:
        print(n)
        datafile = glob.glob('/work/yifan.wang/ringdown/t7-3ogc_fixpsd/data_config_file_3ogc/*'+str(n)+'*.ini')[0]
        t.write('[event-'+str(n)+']\n')
        t.write('label='+str(n)+'\n')
        t.write('config-files='+str(datafile)+'\n')
        t.write('\t\t\t'+kerr_dir+'\n')
        # need ra,dec,final_mass
        ra,dec,final_mass,final_freq,tc,toffset = info(n[2:])
        t.write('config-overrides =static_params:ra:'+str(ra)+'\n')
        t.write('\t\t\tstatic_params:dec:'+str(dec)+'\n')
        t.write('\t\t\tdata:trigger-time:'+str(tc)+'\n')
        if set_toffset:
            t.write('\t\t\tstatic_params:toffset:'+str(toffset)+'\n')
        if final_mass < 150 and final_mass>10:
            t.write('\t\t\tprior-final_mass:min-final_mass:10\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:200\n')
        elif final_mass <= 150:
            t.write('\t\t\tprior-final_mass:min-final_mass:1\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:50\n')
        else:
            t.write('\t\t\tprior-final_mass:min-final_mass:100\n')
            t.write('\t\t\tprior-final_mass:max-final_mass:500\n')

        if final_freq > 1024:
            t.write('\t\t\tdata:sample-rate:4096\n')
        t.write('\n')
t.close()

gw150914_095045
150914_095045
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW150914_095045-PYCBC-POSTERIOR-XPHM.hdf']
gw151012_095443
151012_095443
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW151012_095443-PYCBC-POSTERIOR-XPHM.hdf']
gw151226_033853
151226_033853
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW151226_033853-PYCBC-POSTERIOR-XPHM.hdf']
gw170104_101158
170104_101158
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW170104_101158-PYCBC-POSTERIOR-XPHM.hdf']
gw170121_212536
170121_212536
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW170121_212536-PYCBC-POSTERIOR-XPHM.hdf']
gw170202_135657
170202_135657
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW170202_135657-PYCBC-POSTERIOR-XPHM.hdf']
gw170304_163753
170304_163753
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW170304_163753-PYCBC-POSTERIOR-XPHM.hdf']
gw170403_230611
170403_230611
['/work/yifan.wang/3ogcPE/datarelease/allposterior/GW170403_230611-PYCBC-POSTERIOR-XPHM.hdf']
gw170608